In [95]:
import mt.ml_model_training as training
import mt.resources.ml_funcs as mlf
import numpy as np
import pandas as pd
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import train_test_split, cross_val_score
from sklearn.preprocessing import MinMaxScaler, QuantileTransformer
from sklearn.metrics import fbeta_score
from sklearn.metrics import confusion_matrix, roc_auc_score, make_scorer
from sklearn.inspection import permutation_importance
from sklearn.feature_selection import SelectKBest, mutual_info_classif, f_classif, chi2
from mlxtend.feature_selection import SequentialFeatureSelector as SFS
from imblearn.under_sampling import RandomUnderSampler, ClusterCentroids

In [96]:
strat_name = 'ChannelRun'
side = 'long'
timeframe = '1h'
strat_params = (200, 'edge')
num_pairs = 150
selection_method = '1w_volumes'
thresh = 0.4
data_len = 2500
pairs = mlf.get_margin_pairs(selection_method, num_pairs)
# results = training.create_risk_dataset(strat_name, side, timeframe, strat_params, num_pairs, selection_method, thresh)
results = training.generate_channel_run_dataset(pairs, side, timeframe, strat_params, data_len)

data generation began: 2023/11/09 11:43


In [97]:
results

timestamp        open        high         low       close    base_vol   quote_vol  num_trades  taker_buy_base_vol  taker_buy_quote_vol  ...  weekly_open_ratio  entry_l  entry_s      atr-10       r_pct        rr  lifespan  pnl_pct       pnl_r  pnl_cat
0    2023-07-27 13:00:00+00:00  5.2300e-02  5.2500e-02  5.2100e-02  5.2300e-02  5.3430e+05  2.7936e+04       276.0          3.3010e+05           1.7267e+04  ...             1.0077    False    False  4.5483e-04  4.7631e-04   13.1769       120  -0.0256 -5.3792e+01        0
1    2023-07-27 15:00:00+00:00  9.4200e-01  9.4500e-01  9.3800e-01  9.3900e-01  9.5730e+04  9.0011e+04       454.0          3.6850e+04           3.4680e+04  ...             0.9269    False    False  5.5733e-03  5.3634e-03    8.9711         2  -0.0130 -2.4205e+00        0
2    2023-07-27 16:00:00+00:00  9.3900e-01  9.4000e-01  9.3600e-01  9.3800e-01  8.4080e+04  7.8837e+04       281.0          1.8625e+04           1.7470e+04  ...             0.9260     True    False  5.3634e-03  5.1889e-03   11.9629         1  -0.0107 -2.0583e+00        0
3    2023-07-27 17:00:00+00:00  1.9160e-01  1.9160e-01  1.9070e-01  1.9070e-01  1.0731e+05  2.0506e+04       124.0          4.2739e+04           8.1714e+03  ...             0.9321    False    False  1.2588e-03  1.3996e-03    8.4362       142  -0.0151 -1.0823e+01        0
4    2023-07-27 17:00:00+00:00  5.2500e-02  5.2700e-02  5.2400e-02  5.2400e-02  1.6440e+05  8.6375e+03        85.0          5.9936e+04           3.1486e+03  ...             1.0096    False    False  4.8016e-04  5.1963e-04   12.7088       142  -0.0265 -5.0910e+01        0
5    2023-07-27 17:00:00+00:00  5.2100e-02  5.2200e-02  5.1800e-02  5.2100e-02  3.3493e+06  1.7402e+05       587.0          1.2924e+06           6.7205e+04  ...             1.0296    False    False  4.8106e-04  4.9574e-04   10.0428       104  -0.0223 -4.4903e+01        0
6    2023-07-27 17:00:00+00:00  4.2720e-01  4.2770e-01  4.2540e-01  4.2560e-01  3.6739e+05  1.5663e+05       740.0          1.5524e+05           6.6188e+04  ...             0.9640    False    False  2.7107e-03  3.0550e-03    8.8036       104  -0.0138 -4.5177e+00        0
7    2023-07-27 17:00:00+00:00  9.3800e-01  9.3800e-01  9.3400e-01  9.3600e-01  7.1630e+04  6.7035e+04       286.0          3.9605e+04           3.7087e+04  ...             0.9240     True    False  5.1889e-03  6.1528e-03   11.8977        74  -0.0118 -1.9201e+00        0
8    2023-07-27 18:00:00+00:00  5.2500e-02  5.2500e-02  5.1700e-02  5.2000e-02  7.1985e+05  3.7475e+04       315.0          2.3166e+05           1.2081e+04  ...             1.0019     True    False  5.1963e-04  4.9338e-04   14.2677       115  -0.0241 -4.8780e+01        0
9    2023-07-27 19:00:00+00:00  1.9060e+00  1.9140e+00  1.9020e+00  1.9090e+00  6.6654e+04  1.2720e+05       553.0          3.1237e+04           5.9616e+04  ...             0.8769    False    False  1.6612e-02  1.6889e-02    9.4683        72  -0.0187 -1.1076e+00        0
10   2023-07-27 19:00:00+00:00  5.1900e-02  5.2000e-02  5.1700e-02  5.1900e-02  2.6494e+05  1.3750e+04       150.0          1.6184e+05           8.4024e+03  ...             1.0000     True    False  4.9338e-04  4.5929e-04   13.3703       114  -0.0253 -5.5072e+01        0
11   2023-07-27 21:00:00+00:00  9.2800e-01  9.3100e-01  9.2700e-01  9.2900e-01  8.8251e+04  8.1966e+04       326.0          2.8957e+04           2.6928e+04  ...             0.9171    False    False  5.7664e-03  5.5706e-03    9.0818        70  -0.0144 -2.5878e+00        0
12   2023-07-27 21:00:00+00:00  5.2000e-02  5.2300e-02  5.2000e-02  5.2300e-02  2.5694e+05  1.3398e+04       124.0          1.3997e+05           7.2995e+03  ...             1.0077    False    False  4.4124e-04  4.1450e-04   12.6802       112  -0.0263 -6.3477e+01        0
13   2023-07-28 02:00:00+00:00  5.2000e-02  5.2000e-02  5.1800e-02  5.2000e-02  1.8242e+06  9.4656e+04       395.0          4.3525e+05           2.2608e+04  ...             1.0277    False    False  3.7988e-04  3.

In [102]:
# split features from labels
X = results.drop(['timestamp', 'pnl_pct', 'pnl_r', 'pnl_cat'], axis=1)
y = results.pnl_cat  # pnl > threshold

# balance classes
# us = RandomUnderSampler(random_state=0)
us = ClusterCentroids(random_state=0)
X, y = us.fit_resample(X, y)

original_cols = list(X.columns)  # list of strings, names of all features
X = pd.DataFrame(QuantileTransformer().fit_transform(X), columns=original_cols)

In [103]:
# eliminate features
nan_condition = X.columns[X.isnull().mean(axis=0) < 0.1]
X = X[nan_condition]
variance_condition = X.columns[X.var() > 0.001]
X = X[variance_condition]

In [114]:
# find collinearity
corr_thresh = 0.5
corr_matrix = X.corr()
# Extract the upper triangle of the correlation matrix
upper = corr_matrix.where(np.triu(np.ones(corr_matrix.shape), k=1).astype(bool))

In [115]:
upper

open  quote_vol  atr_z_25  atr_100_pct  ats_z_12  bullish_bar  day_of_week  day_of_week_180  dd_z_12  dd_z_25  ...  rsi_100_above_30  rsi_14_above_50  rsi_timing_l_3_14  skew_6  skew_100  ema_48_above_192  vol_delta  recent_vd_div_1  entry_l  lifespan
open                      NaN     0.1605    0.0114      -0.0852   -0.0381       0.0375       0.0445           0.0035   0.0168   0.0208  ...       -6.6542e-02       9.9266e-02             0.0550 -0.0201   -0.0365            0.0095     0.2384           0.0633   0.0175    0.1988
quote_vol                 NaN        NaN    0.2588       0.3166    0.3019      -0.0092      -0.0336          -0.0254   0.1745   0.1253  ...       -5.6191e-02       4.2374e-02             0.1232 -0.0680   -0.1806            0.1814    -0.1512           0.0256   0.0285   -0.3363
atr_z_25                  NaN        NaN       NaN      -0.1393    0.2601      -0.0767      -0.2948           0.0268   0.2550   0.4007  ...        2.4987e-02      -1.6406e-01             0.1404 -0.1194   -0.2233            0.0744    -0.0678          -0.0463  -0.0808   -0.0757
atr_100_pct               NaN        NaN       NaN          NaN    0.0821       0.1523      -0.0098          -0.0676  -0.0776  -0.1031  ...       -7.6346e-02       1.4946e-01             0.0346  0.0303    0.0182            0.2898    -0.0287           0.0753   0.2217   -0.0517
ats_z_12                  NaN        NaN       NaN          NaN       NaN      -0.0361      -0.0644          -0.0068   0.0959   0.1297  ...       -3.2437e-02      -4.4562e-02             0.0485  0.0148   -0.0210            0.1080    -0.0694          -0.0247   0.0042   -0.1189
bullish_bar               NaN        NaN       NaN          NaN       NaN          NaN      -0.0323          -0.0999  -0.2785  -0.1853  ...        9.7834e-05       2.9490e-01             0.0986 -0.0542    0.0079            0.1703     0.2749           0.3506  -0.0038   -0.0105
day_of_week               NaN        NaN       NaN          NaN       NaN          NaN          NaN          -0.1666  -0.1234  -0.1409  ...       -1.0261e-01       1.4290e-02            -0.1007  0.0492    0.2347           -0.1161     0.0026          -0.0555   0.0069    0.1267
day_of_week_180           NaN        NaN       NaN          NaN       NaN          NaN          NaN              NaN   0.0076   0.0095  ...        3.1983e-02      -1.4036e-01            -0.1142 -0.0459   -0.1923           -0.1024     0.0221          -0.0469  -0.0415    0.0273
dd_z_12                   NaN        NaN       NaN          NaN       NaN          NaN          NaN              NaN      NaN   0.2951  ...        4.3679e-02      -1.2328e-01             0.1718 -0.1735   -0.0271            0.0278    -0.2229          -0.0968   0.1053   -0.1135
dd_z_25                   NaN        NaN       NaN          NaN       NaN          NaN          NaN              NaN      NaN      NaN  ...        7.4043e-02      -2.5963e-01             0.2547 -0.1736   -0.0851            0.0635    -0.1185          -0.0747   0.0650   -0.0297
weighted_50_bull_doji     NaN        NaN       NaN          NaN       NaN          NaN          NaN              NaN      NaN      NaN  ...        3.4131e-02       2.3442e-01             0.3161 -0.0445   -0.1092            0.2411    -0.0255           0.1655   0.0686   -0.1405
weighted_50_bear_doji     NaN        NaN       NaN          NaN       NaN          NaN          NaN              NaN      NaN      NaN  ...        4.3374e-02       3.2387e-01             0.2923  0.0048   -0.0686            0.3395     0.0249           0.2594   0.1567   -0.1469
unweighted_bull_doji      NaN        NaN       NaN          NaN       NaN          NaN          NaN              NaN      NaN      NaN  ...        8.6023e-03       2.2445e-01             0.1658 -0.0274   -0.0246            0.1534     0.0476           0.1955   0.0057    0.0059
unweighted_bear_doji      NaN        NaN       NaN          NaN       NaN          NaN          NaN              NaN      NaN      NaN  ...        

In [116]:

# Select the features with correlations above the threshold
# Need to use the absolute value
to_drop = [column for column in upper.columns if any(upper[column].abs() > corr_thresh)]

In [117]:
to_drop

[]

In [108]:

# Iterate through the columns to drop to record pairs of correlated features
record_collinear = []
for column in to_drop:
    # Find the correlated features
    corr_features = list(upper.index[upper[column].abs() > corr_thresh])

    # Find the correlated values
    corr_values = list(upper[column][upper[column].abs() > corr_thresh])
    drop_features = [column for _ in range(len(corr_features))]

    # # Record the information (need a temp df for now)
    # temp_df = pd.DataFrame.from_dict({'drop_feature': drop_features,
    #                                   'corr_feature': corr_features,
    #                                   'corr_value': corr_values})

    # Add to dataframe
    if drop_features:
        record_collinear.append(drop_features)

collinear_features = set(record_collinear)

In [109]:
collinear_features

drop_feature             corr_feature  corr_value
0                        high                     open      1.0000
1                         low                     open      0.9999
2                         low                     high      0.9999
3                       close                     open      0.9999
4                       close                     high      0.9999
5                       close                      low      1.0000
6                    base_vol                     open     -0.7445
7                    base_vol                     high     -0.7435
8                    base_vol                      low     -0.7469
9                    base_vol                    close     -0.7458
10                 num_trades                quote_vol      0.9666
11         taker_buy_base_vol                     open     -0.7360
12         taker_buy_base_vol                     high     -0.7349
13         taker_buy_base_vol                      low     -0.7383
14         taker_buy_base_vol                    close     -0.7371
15         taker_buy_base_vol                 base_vol      0.9945
16        taker_buy_quote_vol                quote_vol      0.9895
17        taker_buy_quote_vol               num_trades      0.9624
18                       vwma                     open      0.9997
19                       vwma                     high      0.9997
20                       vwma                      low      0.9995
21                       vwma                    close      0.9996
22                       vwma                 base_vol     -0.7398
23                       vwma       taker_buy_base_vol     -0.7311
24                   atr_z_50                 atr_z_25      0.7740
25                  atr_z_100                 atr_z_50      0.6869
26                atr_200_pct              atr_100_pct      0.9848
27                  atr_5_pct               num_trades      0.5297
28                  atr_5_pct              atr_100_pct      0.8262
29                  atr_5_pct              atr_200_pct      0.7944
30                 atr_10_pct              atr_100_pct      0.8691
31                 atr_10_pct              atr_200_pct      0.8344
32                 atr_10_pct                atr_5_pct      0.9859
33                   ats_z_25                 ats_z_12      0.9516
34                   ats_z_50                 ats_z_12      0.8514
35                   ats_z_50                 ats_z_25      0.9632
36                  ats_z_100                 ats_z_12      0.7486
37                  ats_z_100                 ats_z_25      0.8841
38                  ats_z_100                 ats_z_50      0.9676
39                  ats_z_200                 ats_z_12      0.6569
40                  ats_z_200                 ats_z_25      0.7878
41                  ats_z_200                 ats_z_50      0.8787
42                  ats_z_200                ats_z_100      0.9546
43                bearish_bar              bullish_bar     -0.6595
44          chan_mid_ratio_25                atr_5_pct     -0.6611
45          chan_mid_ratio_25               atr_10_pct     -0.6612
46          chan_mid_ratio_50              atr_100_pct     -0.5630
47          chan_mid_ratio_50              atr_200_pct     -0.5235
48          chan_mid_ratio_50                atr_5_pct     -0.6987
49          chan_mid_ratio_50               atr_10_pct     -0.7144
50          chan_mid_ratio_50        chan_mid_ratio_25      0.7803
51         chan_mid_ratio_100              atr_100_pct     -0.7209
52         chan_mid_ratio_100              atr_200_pct     -0.6721
53         chan_mid_ratio_100                atr_5_pct     -0.7160
54         chan_mid_ratio_100               atr_10_pct     -0.7513
55         chan_mid_ratio_100        chan_mid_ratio_25      0.5755
56         chan_mid_ratio_100        chan_mid_ratio_50      0.7529
57          chan_mid_width_25              atr_100_pct      0.7242
58          chan_mid_width_25              atr_200_pct      0.69

In [110]:
drop = list(collinear_features.drop_feature.unique())
len(drop)

161

In [111]:
corr = list(collinear_features.corr_feature.unique())
len(corr)

164

In [113]:
X = X.drop(drop, axis=1)